In [1]:
import pandas as pd
import math

In [2]:
def haversine(lat1, lon1, lat2, lon2):
    R = 6371.0

    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])

    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = math.sin(dlat / 2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))

    distance = R * c
    return distance

In [3]:
def find_nearest_restaurants(df, res, max_distance):
    lats, lons = res['latitude'].tolist(), res['longitude'].tolist()

    for index, row in df.iterrows():
        if pd.notna(row['latitude']) and pd.notna(row['longitude']):
            hotel_lat = float(row['latitude'])
            hotel_lon = float(row['longitude'])

            distances = []
            for res_idx, (lat, lon) in enumerate(zip(lats, lons)):
                distance = haversine(hotel_lat, hotel_lon, lat, lon)
                distances.append((distance, res_idx))

            sorted_dist = sorted(distances, key=lambda x: x[0])
            nearest_restaurant = [item for item in sorted_dist if item[0] <= max_distance]

            restaurant_info = "\n".join(
                f"Nhà hàng: {res.iloc[i]['name']}" +
                (f", Địa chỉ: {res.iloc[i]['address']}" if pd.notna(res.iloc[i]['address']) else "") +
                (f", Khoảng cách: {round(d, 1)} km" if pd.notna(d) else "") +
                (f", Rating: {res.iloc[i]['rating']}" if pd.notna(res.iloc[i]['rating']) else "") +
                (f", Open Hours: {res.iloc[i]['open_hours']}" if pd.notna(res.iloc[i]['open_hours']) else "") +
                (f", Website: {res.iloc[i]['website']}" if pd.notna(res.iloc[i]['website']) else "") +
                (f", Phone: {res.iloc[i]['phone']}" if pd.notna(res.iloc[i]['phone']) else "")
                for d, i in nearest_restaurant
            )
            df.at[index, 'nearest_restaurants'] = restaurant_info
            hotel_info = f"Khách sạn: {row['hotel_name']}\nCác nhà hàng gần nhất:\n{restaurant_info}"
            # print(hotel_info)

In [4]:
df_hotel = pd.read_csv("../data/hotel_final.csv")
df_restaurant = pd.read_csv("../data/restaurant_final.csv")

In [5]:
find_nearest_restaurants(df_hotel, df_restaurant, 10)

Khách sạn: DeLaSea Phát Linh Hạ Long
Các nhà hàng gần nhất:
Nhà hàng: Ăn Đêm Đồ Nhậu, Địa chỉ: Quốc Lộ 18 Đại Yên 01124 Quảng Ninh, Khoảng cách: 2.1 km
Nhà hàng: Nhà Hàng Quỳnh Ngọc, Địa chỉ: 574,Quốc Lộ 18 Hà Khẩu 01122 Quảng Ninh, Khoảng cách: 2.7 km
Nhà hàng: Marina Restaurant, Địa chỉ: Tuan Chau Ward Halong Bay Quang Ninh, Khoảng cách: 4.9 km, Rating: 4.5, Open Hours: Open · Closes 6 PM, Phone: 091 253 40 36
Nhà hàng: Nhà Hàng Vân Anh, Địa chỉ: Quốc Lộ 18 Hà Khẩu 01122 Quảng Ninh, Khoảng cách: 5.0 km, Phone: 090 222 13 69
Nhà hàng: Nhà Hàng Lâm Hải, Địa chỉ: Số 2 Đ. Hoàng Quốc Việt, Bãi Cháy, Thành phố Hạ Long, Quảng Ninh, Việt Nam, Khoảng cách: 5.6 km, Phone: 090 329 61 89
Nhà hàng: Nhà Hàng Hồng Hạnh 6, Địa chỉ: Đường Hoàng Quốc Việt Hùng Thắng 01120 Quảng Ninh, Khoảng cách: 6.0 km
Nhà hàng: Vui Long Khach Den, Địa chỉ: Ngoc Chau, Tuan Chau Island Ha Long, Khoảng cách: 6.6 km
Nhà hàng: Bep Viet, Địa chỉ: So 1 Ngo Bao Kanh, Hang Trong Hanoi, Khoảng cách: 7.2 km, Rating: 5.0
Nhà hà

In [6]:
df_hotel.to_csv("../data/hotel_with_nearest_restaurants.csv", index=False)